In [32]:
# write a diagnostics function that takes input M and returns a matrix with common Gibbs Sampler diagnostics
###############################################################################################################
# you can copy and call this function for all future applications that produce GS draws
def kdiagnostics(M):

    k = shape(M)[0] # row dimension in this case
    R = shape(M)[1]  #column dimension, OK to re-use "R" as it is local
    
    #######################################
    # Autocorrelation, nse, and efficiency
    #######################################
    IEF = zeros([k,1]) #will collect IEF scores for each coefficient
    nse = zeros([k,1]) #will collect nse values for each coefficient

    for i in range(0,k):  #Golden rule for loops: subtract 1 from intended starting point, keep endpoint
        int0 = M[i,:] # pick draws for a single parameter; 
        # here we don't need a 2-dim vector, so no need to write M[i-1:i,:]
        intsum = 0
        #print("intsum start =", intsum)
        #j=0
        for j in range (1,(R-1)):   #same as 1:(R-2) in R; here I start at "1' since j is used in division below
            int1 = int0[0:(R-j)]       #same as 1:(R-j) in R
            int2 = int0[j:R]           #same as (j+1):R in R
            int3 = corrcoef(int1,int2)[0,1] #corcoeff produces a 2 x 2 so get the offdiagonal
            intsum = intsum + (1-(j/R))*int3 #OK here since j starts at 1
            #print("intsum update=", intsum)
            if abs(int3)<0.05:
                #print("j=", j)
                break # exit innermost loop
        intsum = max(0,intsum) #for situations when the loop immediately cuts off 
        # with a slight negative value for the correlation
        IEF[i] = 1+2*intsum
        #print(i)

    #print("end of IEF loop")
    
    # Obtain numerical standard error (nse) and "equivalent itertions" (m*)
    tt = diag(cov(M))
    tt.shape=(k,1) #need to add second dimension, else trouble
    nse = sqrt(((1/R)*(tt*IEF))) #note: in Python, cov() considers each ROW a variable
    
    mstar = R/IEF
    
    ###############################
    # CD diagnostics
    ###############################
    g1 = round(0.1*R) #capture initial 10% set of draws
    g2 = round(0.6*R)+1 #capture final 40% set of draws
    M1 = M[:,0:g1]   #cut off first 10% of columns
    M2 = M[:,g2-1:R] #cut off last 40% of columns
    R1 = shape(M1)[1] #capture number of columns
    R2 = shape(M2)[1]

    #
    IEF1 = zeros([k,1]) 
    nse1 = zeros([k,1])
    #
    for i in range(0,k):  #Golden rule for loops: subtract 1 from intended starting point, keep endpoint
        int0 = M1[i,:] # pick draws for a single parameter; 
        # here we don't need a 2-dim vector, so no need to write M[i-1:i,:]
        intsum = 0
        #print("intsum start =", intsum)
        #j=0
        for j in range (1,(R1-1)):   #same as 1:(R-2) in R; here I start at "1' since j is used in division below
            int1 = int0[0:(R1-j)]       #same as 1:(R-j) in R
            int2 = int0[j:R1]           #same as (j+1):R in R
            int3 = corrcoef(int1,int2)[0,1] #corcoeff produces a 2 x 2 so get the offdiagonal
            intsum = intsum + (1-(j/R1))*int3 #OK here since j starts at 1
            #print("intsum update=", intsum)
            if abs(int3)<0.05:
                #print("j=", j)
                break # exit innermost loop
        intsum = max(0,intsum) #for situations when the loop immediately cuts off 
        # with a slight negative value for the correlation
        IEF1[i] = 1+2*intsum
        
    nse1 = sqrt(((1/R1)*(tt*IEF1)))
        
          #
    IEF2 = zeros([k,1])
    nse2 = zeros([k,1])
        
    for i in range(0,k):  #Golden rule for loops: subtract 1 from intended starting point, keep endpoint
        int0 = M2[i,:] # pick draws for a single parameter; 
        intsum = 0
        #print("intsum start =", intsum)
        #j=0
        for j in range (1,(R2-1)):   #same as 1:(R-2) in R; here I start at "1' since j is used in division below
            int1 = int0[0:(R2-j)]       #same as 1:(R-j) in R
            int2 = int0[j:R2]           #same as (j+1):R in R
            int3 = corrcoef(int1,int2)[0,1] #corcoeff produces a 2 x 2 so get the offdiagonal
            intsum = intsum + (1-(j/R2))*int3 #OK here since j starts at 1
            #print("intsum update=", intsum)
            if abs(int3)<0.05:
                #print("j=", j)
                break # exit innermost loop
        intsum = max(0,intsum) #for situations when the loop immediately cuts off 
        # with a slight negative value for the correlation
        IEF2[i] = 1+2*intsum
        
    nse2 = sqrt(((1/R2)*(tt*IEF2)))
    
    # compute CD diagnostic
    #################################
    mM1 = matrix(M1.mean(1)).T #mean across columns, 1-dimensional, but matrix wrapper & transpose make it a column
    mM2 = matrix(M2.mean(1)).T
    
    CD = (mM1-mM2)/(sqrt(nse1**2 + nse2**2))
    
    ################################
    # p>0 statistic
    #################################
    p0vec=zeros([k,1])
    for i in range(0,k):
        int0 = M[i,:]
        int1 = int0[int0>0]
        p0vec[i] = len(int1)/R
    
    
    mM = matrix(M.mean(1)).T
    mstd = matrix(M.std(1)).T
    diagnostics = concatenate((mM,mstd,p0vec,nse,IEF,mstar,CD),axis=1)
    
    return(diagnostics)